# Análise Database Olist 
Este projeto proporciona uma visão abrangente do ecossistema de vendas da Olist, permitindo a identificação de padrões de comportamento dos consumidores e o desempenho dos vendedores, contribuindo para a tomada de decisões estratégicas baseadas em dados.
# Autoria: @pedroblaschi   -  [linkedin](https://www.linkedin.com/in/pedro-blaschi-a3b5b22a9/)  -  [github](https://github.com/blaschis/blaschis) <p>

### Importando 

In [0]:
df1 = spark.read.format("csv").option("header", "true").load("dbfs:/FileStore/shared_uploads/pedroblaschis@gmail.com/olist_customers_dataset-1.csv")
df2 = spark.read.format("csv").option("header", "true").load("dbfs:/FileStore/shared_uploads/pedroblaschis@gmail.com/olist_order_items_dataset-1.csv")
df3 = spark.read.format("csv").option("header", "true").load("dbfs:/FileStore/shared_uploads/pedroblaschis@gmail.com/olist_order_payments_dataset-1.csv")
df4 = spark.read.format("csv").option("header", "true").load("dbfs:/FileStore/shared_uploads/pedroblaschis@gmail.com/olist_order_reviews_dataset-1.csv")
df5 = spark.read.format("csv").option("header", "true").load("dbfs:/FileStore/shared_uploads/pedroblaschis@gmail.com/olist_geolocation_dataset-1.csv")
df6 = spark.read.format("csv").option("header", "true").load("dbfs:/FileStore/shared_uploads/pedroblaschis@gmail.com/olist_products_dataset-1.csv")
df7 = spark.read.format("csv").option("header", "true").load("dbfs:/FileStore/shared_uploads/pedroblaschis@gmail.com/olist_orders_dataset-1.csv")
df8 = spark.read.format("csv").option("header", "true").load("dbfs:/FileStore/shared_uploads/pedroblaschis@gmail.com/olist_sellers_dataset-1.csv")
df9 = spark.read.format("csv").option("header", "true").load("dbfs:/FileStore/shared_uploads/pedroblaschis@gmail.com/product_category_name_translation-1.csv")

In [0]:
print(df1.head())

Row(customer_id='06b8999e2fba1a1fbc88172c00ba8bc7', customer_unique_id='861eff4711a542e4b93843c6dd7febb0', customer_zip_code_prefix='14409', customer_city='franca', customer_state='SP')


### Database

In [0]:
# Especificar o banco de dados
spark.sql("USE olist")

# Salvar os DataFrames no banco de dados
df1.write.mode("overwrite").saveAsTable("olist.olist_customers")
df2.write.mode("overwrite").saveAsTable("olist.olist_order_items")
df3.write.mode("overwrite").saveAsTable("olist.olist_order_payments")
df4.write.mode("overwrite").saveAsTable("olist.olist_order_reviews")
df5.write.mode("overwrite").saveAsTable("olist.olist_geolocation")
df6.write.mode("overwrite").saveAsTable("olist.olist_products")
df7.write.mode("overwrite").saveAsTable("olist.olist_orders")
df8.write.mode("overwrite").saveAsTable("olist.olist_sellers")
df9.write.mode("overwrite").saveAsTable("olist.product_category_translation")

In [0]:
%sql
SHOW TABLES IN olist;

database tableName isTemporary olist olist_customers false olist olist_geolocation false olist olist_order_items false olist olist_order_payments false olist olist_order_reviews false olist olist_orders false olist olist_products false olist olist_sellers false olist product_category_translation false olist vw_categorias_mais_vendidas false olist vw_desempenho_vendedores false olist vw_pedidos_por_cliente false olist vw_produtos_mais_vendidos false olist vw_tempo_entrega_avaliacao false olist vw_valor_total_pedidos_por_cliente false

In [0]:
%sql
SELECT * FROM olist_customers LIMIT 10;
SELECT * FROM olist_geolocation LIMIT 10;
SELECT * FROM olist_order_items LIMIT 10;
SELECT * FROM olist_order_payments LIMIT 10;
SELECT * FROM olist_order_reviews LIMIT 10;
SELECT * FROM olist_orders LIMIT 10;
SELECT * FROM olist_products LIMIT 10;
SELECT * FROM olist_sellers LIMIT 10;
SELECT * FROM product_category_translation LIMIT 10;

product_category_name product_category_name_english beleza_saude health_beauty informatica_acessorios computers_accessories automotivo auto cama_mesa_banho bed_bath_table moveis_decoracao furniture_decor esporte_lazer sports_leisure perfumaria perfumery utilidades_domesticas housewares telefonia telephony relogios_presentes watches_gifts

### Limpeza

In [0]:
# Função limpeza
def clean_spark_dataframe(df):
    # Remover duplicados
    df = df.dropDuplicates()
    
    # Remover colunas vazias
    non_empty_cols = [col for col in df.columns if df.filter(df[col].isNotNull()).count() > 0]
    df = df.select(non_empty_cols)
    
    # Remover linhas com valores nulos
    df = df.na.drop(how='any')
    
    return df

# Aplicar a função de limpeza a todos os dataframes
df1 = clean_spark_dataframe(df1)
df2 = clean_spark_dataframe(df2)
df3 = clean_spark_dataframe(df3)
df4 = clean_spark_dataframe(df4)
df5 = clean_spark_dataframe(df5)
df6 = clean_spark_dataframe(df6)
df7 = clean_spark_dataframe(df7)
df8 = clean_spark_dataframe(df8)
df9 = clean_spark_dataframe(df9)

In [0]:
%sql
-- Corrigir os dados de datas para timestamp
CREATE OR REPLACE VIEW VW_TEMPO_ENTREGA_AVALIACAO AS
SELECT 
    O.order_id,
    CAST(O.order_delivered_customer_date AS TIMESTAMP) AS order_delivered_customer_date,
    CAST(O.order_estimated_delivery_date AS TIMESTAMP) AS order_estimated_delivery_date,
    R.review_score,
    DATEDIFF(
        CAST(O.order_delivered_customer_date AS TIMESTAMP), 
        CAST(O.order_estimated_delivery_date AS TIMESTAMP)
    ) AS dias_atraso
FROM 
    olist_orders AS O
INNER JOIN 
    olist_order_reviews AS R ON O.order_id = R.order_id
WHERE 
    O.order_delivered_customer_date IS NOT NULL
    AND O.order_estimated_delivery_date IS NOT NULL;

In [0]:
%sql
-- Corrigir os dados de avaliações para timestamp
CREATE OR REPLACE VIEW VW_TEMPO_ENTREGA_AVALIACAO AS
SELECT 
    O.order_id,
    CAST(O.order_delivered_customer_date AS TIMESTAMP) AS order_delivered_customer_date,
    CAST(O.order_estimated_delivery_date AS TIMESTAMP) AS order_estimated_delivery_date,
    R.review_score,
    ABS(DATEDIFF(
        CAST(O.order_delivered_customer_date AS TIMESTAMP), 
        CAST(O.order_estimated_delivery_date AS TIMESTAMP)
    )) AS dias_atraso
FROM 
    olist_orders AS O
INNER JOIN 
    olist_order_reviews AS R ON O.order_id = R.order_id
WHERE 
    O.order_delivered_customer_date IS NOT NULL
    AND O.order_estimated_delivery_date IS NOT NULL;

In [0]:
%sql
-- Convertendo review score para inteiro e corrigindo dias de atraso
CREATE OR REPLACE VIEW VW_TEMPO_ENTREGA_AVALIACAO AS
SELECT 
    O.order_id,
    CAST(O.order_delivered_customer_date AS TIMESTAMP) AS order_delivered_customer_date,
    CAST(O.order_estimated_delivery_date AS TIMESTAMP) AS order_estimated_delivery_date,
    CAST(R.review_score AS INT) AS review_score, 
    ABS(DATEDIFF(
        CAST(O.order_delivered_customer_date AS TIMESTAMP), 
        CAST(O.order_estimated_delivery_date AS TIMESTAMP)
    )) AS dias_atraso  
FROM 
    olist_orders AS O
INNER JOIN 
    olist_order_reviews AS R ON O.order_id = R.order_id
WHERE 
    O.order_delivered_customer_date IS NOT NULL
    AND O.order_estimated_delivery_date IS NOT NULL;

### Consultas

In [0]:
%sql
-- Relação cliente/pedido

CREATE VIEW VW_PEDIDOS_POR_CLIENTE AS
SELECT O.*, C.customer_city, C.customer_state
FROM olist_orders AS O
INNER JOIN olist_customers AS C
ON O.customer_id = C.customer_id;

In [0]:
%sql
SELECT * FROM VW_PEDIDOS_POR_CLIENTE LIMIT 100;

order_id customer_id order_status order_purchase_timestamp order_approved_at order_delivered_carrier_date order_delivered_customer_date order_estimated_delivery_date customer_city customer_state d9eabc69f974b3d088e991cb7a7f08cd d4be0795e8fa7ea792920e04f7fba7eb delivered 2018-03-21 19:32:50 2018-03-21 19:48:04 2018-03-22 19:48:46 2018-03-28 18:56:52 2018-04-13 00:00:00 sao paulo SP c9fbf88f9c58364e0434971962dc1a53 7ec5b53960d508118d7a3126af968d44 delivered 2018-02-05 16:47:14 2018-02-05 17:16:09 2018-02-07 15:04:45 2018-02-20 19:59:00 2018-03-12 00:00:00 teresopolis RJ fd01a48a7d75383a3623e71a538584c3 014f2d069b53eec84aed9b8c1d5ef270 delivered 2017-08-18 14:17:44 2017-08-18 14:35:12 2017-08-25 15:32:02 2017-08-28 17:04:11 2017-08-31 00:00:00 carapicuiba SP 6d4616de4341417e17978fe57aec1c46 adc1b0d30fe2b52bde12fe806630d54f delivered 2017-04-15 11:46:19 2017-04-15 12:02:55 2017-04-19 08:18:54 2017-05-05 15:56:20 2017-05-24 00:00:00 uniao de minas MG c606769bddf9fb8b9f949b128133c463 a4b29e455132615d47ab1751f4158252 delivered 2017-06-15 13:17:07 2017-06-17 03:45:11 2017-06-20 10:54:02 2017-06-23 13:14:54 2017-07-10 00:00:00 vitoria ES 5ef95d0a45b4caaaa70e601665ba1a6a 11862cf00ec1d9f5067508ecf1252790 delivered 2017-04-17 21:38:31 2017-04-18 02:15:13 2017-04-18 08:51:11 2017-05-15 08:17:43 2017-05-24 00:00:00 quixada CE 9f2fe2350791b5e9e62610331d125843 208dce5ddbcf741af0c04f0a72a4d08e delivered 2018-05-03 22:21:53 2018-05-05 02:30:07 2018-05-07 09:10:00 2018-05-10 13:08:57 2018-05-23 00:00:00 sao caetano do sul SP 86bf07c0a6d01d38dd8ecd1a1b68d139 491b9b3d90d1ad0c5ba4e621878d2d56 delivered 2017-09-17 22:44:26 2017-09-17 23:20:49 2017-09-19 22:07:51 2017-09-26 18:33:42 2017-10-17 00:00:00 sao jose do rio pardo SP 2eb455a9ac809470168098ddf4e2a25b 6c26787bd0d839f80a4450e527d0586b delivered 2017-11-05 21:59:14 2017-11-05 22:10:55 2017-11-06 19:18:39 2017-11-09 14:55:57 2017-11-24 00:00:00 tiete SP 5e4d2d8a6589ec90d1c82d0c2cb55eb0 3df001627683ff649e8df47730d2b52c delivered 2017-11-26 15:51:16 2017-11-26 17:16:05 2017-11-27 18:14:56 2017-11-30 01:14:36 2017-12-11 00:00:00 sao paulo SP 098a8457920d6c63f0cb10ccfbcd369d f6a623ccb7b0dac8b9c9c74594f2c041 delivered 2018-06-07 22:58:16 2018-06-09 02:57:45 2018-06-11 14:50:00 2018-06-12 12:41:20 2018-06-25 00:00:00 sorocaba SP 11d410c3e9ae90f2956cf43741d93347 6f08e59327aaa16ee28f5904d596a05a delivered 2018-01-03 11:53:11 2018-01-03 12:07:13 2018-01-03 20:18:35 2018-01-09 15:59:34 2018-01-29 00:00:00 belo horizonte MG f66696cb1765edf51ab4e07f41687f9e 5c1bbb8c8c2ba7ed55150827c25c4b7f delivered 2017-10-22 15:03:58 2017-10-23 17:36:03 2017-10-24 16:58:04 2017-11-07 23:41:55 2017-11-22 00:00:00 fortaleza CE c55fbaf625bec4b8ee5e7b0e8929bbc6 7164a31758114ae20ec36fab61923c51 delivered 2018-03-15 14:39:28 2018-03-15 14:55:43 2018-03-16 19:34:57 2018-03-21 19:40:44 2018-04-03 00:00:00 aracatuba SP b90dbb242e04b393fad2f1df17bc90dc c08451aea5147d7bfe2f21b8bc444d76 delivered 2017-07-21 12:52:35 2017-07-21 13:05:18 2017-07-25 22:19:33 2017-07-27 19:27:47 2017-08-11 00:00:00 aruja SP c11e1e377e956e9d5bec2b0fa2ddc067 d53b4f45e70cf4ffa40c191672179c64 delivered 2018-06-18 21:39:42 2018-06-19 09:58:08 2018-06-20 12:49:00 2018-07-04 22:18:33 2018-07-17 00:00:00 salvador BA 96a5b82a5f7b31928a21f1fe875e1caa 5310ae71dd819077e7b2ec40525d1110 delivered 2017-06-15 17:29:21 2017-06-17 03:44:03 2017-06-19 09:36:29 2017-06-26 12:17:21 2017-07-12 00:00:00 florianopolis SC ff36f4d6d98c0b2a7e70acb7d1b3f139 5cec9498555333d107bea6a6ccd9e2f9 delivered 2017-03-23 18:25:38 2017-03-23 18:35:16 2017-03-24 12:39:56 2017-04-05 14:13:11 2017-04-18 00:00:00 guapore RS 3692c711f70b60feeedb43ae77e87980 1f18b71a69fbba019ef55947129c7f84 delivered 2018-02-08 13:54:12 2018-02-08 14:10:29 2018-02-09 00:49:13 2018-02-16 12:28:56 2018-03-09 00:00:00 boa esperanca MG c01eede39735860e68ef74a1d9ddf5cb 2010323a22f8ea51174a746875bd36c9 delivered 2017-12-20 19:18:39 2017-12-20 19:30:34 2017-12-22 18:58:59 2017-12-27 18:54:45 2018-01-16 00:00:00 belo horizo

Esta consulta oferece uma visão do comportamento de compra dos clientes, analisando o valor total dos pedidos e o número de pedidos por cliente, agrupados por cidade e estado. É útil para identificar quais regiões têm clientes mais ativos e que geram mais receita, fornecendo dados valiosos para estratégias de segmentação geográfica e campanhas de marketing direcionadas.

In [0]:
%sql
-- Valor total de pedidos por cliente

CREATE OR REPLACE VIEW VW_VALOR_TOTAL_PEDIDOS_POR_CLIENTE AS
SELECT 
    C.customer_id,
    C.customer_city,
    C.customer_state,
    COUNT(O.order_id) AS num_pedidos,
    SUM(P.payment_value) AS valor_total_pedidos
FROM 
    olist_orders AS O
INNER JOIN 
    olist_customers AS C ON O.customer_id = C.customer_id
INNER JOIN 
    olist_order_payments AS P ON O.order_id = P.order_id
GROUP BY 
    C.customer_id, C.customer_city, C.customer_state;

In [0]:
%sql
SELECT * FROM VW_VALOR_TOTAL_PEDIDOS_POR_CLIENTE;

customer_id customer_city customer_state num_pedidos valor_total_pedidos 7a503ab0d71429773305ec84d3461e60 brasilia DF 1 180.98 b3ebc63c630e8af49ff5cba1f321928e assis SP 1 135.0 62c11d5a0b49aaf81297d26b0bd9fb8f cariacica ES 1 71.14 243006bde78b37ee1cc3a24727e8f5de indaiatuba SP 1 100.83 5a799d964e08de8aba5211f380a2d988 sao paulo SP 1 23.29 3c296b3dc1d4b9cefdc9bc53a4f847e7 sao paulo SP 1 71.75 0fb2d5ea71450c62f5a0c94c0fb18de9 guaruja SP 1 128.04 436d8d2e5fe73615769631a44e78e06b alem paraiba MG 1 65.0 0faf52fb32003ad8ca5853afe236ac71 sao paulo SP 1 140.33 caedd3b1bebfca71c001c276fb477fa2 rio bonito RJ 1 141.73 053bc4c013d7589b292fe166ecba6786 goiania GO 1 55.37 0afa45aa9b2befa48d4056a9037aeaaf uberaba MG 1 72.43 6c84262d46fe370972acbf13ad5f97c8 rio de janeiro RJ 1 66.64 e26c19c5ccc698f3612f11874d3b07cf campinas SP 1 315.61 3815d8ec9fb5f5ced1a178698eab8acf niteroi RJ 1 122.5 d797148a7505e4d0976f5b61d1c40741 sorocaba SP 1 219.63 369f91f6fec269279e15291df339ce97 tramandai RS 1 149.4 8f7076e6c2a866bb901bc35ada1f96c2 monte alto SP 1 56.01 4312276d4e4b3007a437693e5a39887d sao paulo SP 1 127.99 900d252388a6177a68f549e428fe667f juiz de fora MG 1 94.11 8205033143e83aeee71e4df23fedc372 guarulhos SP 1 95.76 03c23ab69d584dbbed60003db778135d duque de caxias RJ 1 86.83 d2d1c74bca444a6750b9ac7de001953c perdigao MG 1 63.13 e019c5cece8b3842ed7335d88bdab190 santo antonio de jesus BA 1 540.02 dde388ccd1b81511edd5cbebe81aef1e manhuacu MG 1 43.09 eaef21c024d74335f9cce35c9d96958d santos SP 1 158.76 3da151283555f08ba83a9bafed7a269d sao paulo SP 1 157.21 b115955f333cd97a8f4ca448caf47e45 curitiba PR 1 177.67 b125d7ca2bf699633dcec206ec51ce90 jaguariaiva PR 1 68.35 01945b2f58c2f472fb2a5a582f8042c0 capao do cipo RS 1 206.72 30f3b26a06e5a67682305298f83e6be3 redencao PA 2 199.06 5e05e1280df37ecd4d1d46e63c720a36 vila velha ES 1 133.69 acf9d493618557e6bf542739f7c1ea8c sao gotardo MG 1 177.49 290ee0188edbd0ea99a9bcde6c7d8e1b toledo PR 1 77.57 80cb3c3b83d869aba61142daa276a508 sao paulo SP 1 116.75 17c409b1b344d18246c102be4419c73b rio de janeiro RJ 1 60.42 b09883a38c50f6a64741985bd80ec237 presidente dutra MA 1 129.98 ed06bdbc21c55e3174bb8aae5e36366e araraquara SP 1 107.44 25fa6948d92c513abe0352d98d668747 osasco SP 1 35.45 14b6f4189d383785662ff6bf3a9c32e3 sao manuel SP 1 634.91 7faf9c260f51ec1b1e441defba82da35 santo andre SP 1 32.43 f838e842c0f8bda43a21d146deb6f087 campo grande MS 1 149.14 e26eb46e8146dedecc6524e5d9771047 osasco SP 1 139.56 87cfbc9db7f2dc260b8f0022377909ef sao paulo SP 1 54.17 6f0ab5342faa11fb372c28c756d4fd9c sao paulo SP 1 76.1 eaa701838126e86dd60ee4e44d274f21 itajuba MG 1 172.84 032ecf6afa4af219d338d03dd4f80f65 piracicaba SP 1 118.67 c7e04083bffe04edab6d27fb982dc6cc sao paulo SP 13 186.92000000000002 d75b9db917b3486c58876ce6ebe25746 pombal PB 1 223.08 ba9fa21d16fa22ad6a806358b58e2be0 sao paulo SP 1 79.33 95e27d868269c41e9785c6028f1cc504 jaragua do sul SC 1 166.05 54224cb0ac10a018b2dbc51d4a8d89f5 fortaleza CE 1 102.78 ea6ba2b2e27f7efea73bdeab7fd6e4a0 novo horizonte SP 1 157.86 66a4949b286c198a1894aa79014469aa sao paulo SP 1 88.65 5ce0619a7329b660555979b32001ccfd sabara MG 1 459.63 3cc85f62deb4a6349f8f6ecd7d688eb2 joinville SC 1 74.97 49ecca4958a673be112cbe3549795fab lorena SP 1 83.9 3ea02d8ec736f8f94fcdcf7d43bbfb92 sao paulo SP 1 116.99 eabc7351650d54e0a39b2869b6f0d958 sao paulo SP 1 60.86 56e1189772b79e5a9f717ed219371205 cachoeira do sul RS 1 201.75 0ea1ae45d45f7ee83bb2d6eb0c1fd03c goiania GO 1 78.77 5415819ad5ed256b3851eabbbbfe25aa mage RJ 1 73.15 a95ad7bcbf76f95fcb884dfdfa84ae68 vitoria de santo antao PE 1 657.63 4cd906a5d8555340aee749b3a3a3b5d5 alfenas MG 1 274.84 f159cc6c8e0c4582c3580cf716db5237 cajamar SP 1 23.77 877b18b6aaa2faadfbf88c43a9bd5c42 sao paulo SP 1 164.66 d100e821d7b6305bc22190c0a7f0d1de salvador BA 1 67.05 08ae5f06d0fd2ab8acb2fd7263ac0c9d curitiba PR 1 384.5 4aa97f509896f79aa3ca9dd294f02990 parnamirim RN 1 84.54 d884f544da907f4cc6ffc6504f6a27c5 capitao eneas MG 1 98.84 40c7d59d0ca882ee31615c188ee54593 jau SP 1 208.71 90d4df218c9

Databricks visualization. Run in Databricks to view.

Esta consulta identifica os produtos mais vendidos em cada estado e o valor total gerado pelas vendas. Com este insight, podes ver quais produtos são mais populares em diferentes regiões, ajudando na gestão de inventário, estratégias de vendas locais e decisões de marketing com base no interesse regional.

In [0]:
%sql
-- Relação produtos mais vendidos e valor total das vendas

CREATE OR REPLACE VIEW VW_PRODUTOS_MAIS_VENDIDOS AS
SELECT 
    P.product_id,
    PR.product_category_name,
    C.customer_state,
    COUNT(P.product_id) AS quantidade_vendida,
    SUM(P.price) AS valor_total_vendido
FROM 
    olist_order_items AS P
INNER JOIN 
    olist_products AS PR ON P.product_id = PR.product_id
INNER JOIN 
    olist_orders AS O ON P.order_id = O.order_id
INNER JOIN 
    olist_customers AS C ON O.customer_id = C.customer_id
GROUP BY 
    P.product_id, PR.product_category_name, C.customer_state
ORDER BY 
    valor_total_vendido DESC;

In [0]:
%sql
SELECT * FROM VW_PRODUTOS_MAIS_VENDIDOS;

product_id product_category_name customer_state quantidade_vendida valor_total_vendido bb50f2e236e5eea0100680137654686c beleza_saude SP 68 22280.0 99a4788cb24856965c36a24e339b6058 cama_mesa_banho SP 231 20312.279999999995 aca2eb7d00ea1a7b8ebd4e68314663af moveis_decoracao SP 265 18905.6 d6160fb7873f184099d9bc95e30376af pcs SP 11 15499.659999999998 5f504b3a1c75b73d6151be81eb05bdc9 cool_stuff SP 25 15059.3 d1c427060a0f73f6b889a5c7c61f2ac4 informatica_acessorios RJ 102 14724.529999999995 fd0065af7f09af4b82a0ca8f3eed1852 automotivo SP 7 13999.93 5769ef0a239114ac3a854af00df129e4 telefonia_fixa RJ 8 13440.0 53b36df67ebb7c41585e8d54d6772e08 relogios_presentes SP 111 13387.490000000002 e0d64dcfaa3b6db5c54ca298ae101d05 relogios_presentes SP 82 13003.980000000003 87feb07adc221a4c6cdf051ea1afd0ff eletrodomesticos_2 RJ 6 12660.0 d285360f29ac7fd97640bf0baef03de0 relogios_presentes SP 47 11968.67 16c4e87b98a9370a9cbc3a4658a3f45b instrumentos_musicais SP 6 11572.0 588531f8ec37e7d5ff5b7b22ea0488f8 pcs MG 8 11496.0 3dd2a17168ec895c781a9191c1e95ad7 informatica_acessorios SP 75 11242.500000000004 f1c7f353075ce59d8a6f3cf58f419c9c cama_mesa_banho SP 57 11155.9 25c38557cf793876c5abdd5931f922db bebes SP 11 11135.89 d1c427060a0f73f6b889a5c7c61f2ac4 informatica_acessorios MG 82 11130.669999999998 bc4cd4da98dd128c39bf0b8c2674032f pcs SP 8 10099.699999999999 f819f0c84a64f02d3a5606ca95edd272 relogios_presentes SP 16 10079.89 422879e10f46682990de24d770e7f83d ferramentas_jardim SP 181 9870.780000000006 7a10781637204d8d10485c71a6108a2e relogios_presentes SP 46 9862.700000000003 6cdd53843498f92890544667809f1595 beleza_saude SP 25 8738.9 3dd2a17168ec895c781a9191c1e95ad7 informatica_acessorios MG 58 8694.200000000003 53b36df67ebb7c41585e8d54d6772e08 relogios_presentes RJ 75 8617.79 2b4609f8948be18874494203496bc318 beleza_saude SP 97 8428.939999999999 8a12c0e223d9dbd49ccfcd2ad25d1b30 construcao_ferramentas_construcao SP 4 8100.0 dd113cb02b2af9c8e5787e8f1f0722f6 esporte_lazer MG 2 7749.0 6f3b5b605d91b7439c5e3f5a8dffeea7 relogios_presentes SP 48 7736.7 f4f67ccaece962d013a4e1d7dc3a61f7 automotivo SP 33 7715.099999999999 368c6c730842d78016ad823897a372db ferramentas_jardim SP 135 7307.400000000003 389d119b48cf3043d311335e499d9c6b ferramentas_jardim SP 133 7307.2000000000035 6cdd53843498f92890544667809f1595 beleza_saude MG 21 7274.299999999999 4fcb3d9a5f4871e8362dfedbdb02b064 automotivo SP 50 7189.999999999998 19936fa4f614ee0590d3b77ac83fd648 telefonia_fixa ES 4 7160.0 1a080577618e7fe4d9ddd8fb2b47a964 relogios_presentes SP 12 7020.99 f49e985b4cb2d0543890d6dd00077663 portateis_casa_forno_e_cafe SP 9 6955.0 bb50f2e236e5eea0100680137654686c beleza_saude CE 21 6880.0 bb50f2e236e5eea0100680137654686c beleza_saude MG 21 6850.0 52c80cedd4e90108bf4fa6a206ef6b03 ferramentas_jardim RJ 39 6736.84 489ae2aa008f021502940f251d4cce7f utilidades_domesticas MS 1 6735.0 69c590f7ffc7bf8db97190b6cb6ed62e pcs ES 1 6729.0 bee2e070c39f3dd2f6883a17a5f0da45 informatica_acessorios SP 39 6660.0 af51d485dc5255ba2e18b21b550156e6 malas_acessorios SP 25 6656.68 d1c427060a0f73f6b889a5c7c61f2ac4 informatica_acessorios SP 49 6644.76 44fc450365728c413fefc547592626be eletroportateis SP 8 6643.0 53759a2ecddad2bb87a079a1f1519f73 ferramentas_jardim SP 121 6538.300000000003 461f43be3bdf8844e65b62d9ac2c7a5a relogios_presentes SP 45 6517.1900000000005 1bdf5e6731585cf01aa8169c7028d6ad artes SP 1 6499.0 a62e25e09e05e6faf31d90c6ec1aa3d1 relogios_presentes SP 61 6471.0 25292482a61cb3298df8dbe15ea69daf beleza_saude SP 5 6448.250000000001 0a57f7d2c983bcf8188589a5fea4a8da relogios_presentes SP 58 6367.000000000001 165f86fe8b799a708a20ee4ba125c289 cool_stuff SP 39 6341.61 35afc973633aaeb6b877ff57b2793310 casa_conforto SP 72 6319.090000000002 52c80cedd4e90108bf4fa6a206ef6b03 ferramentas_jardim MG 36 6304.89 e53e557d5a159f5aa2c5e995dfdf244b informatica_acessorios SP 73 6136.210000000001 99a4788cb24856965c36a24e339b6058 cama_mesa_banho RJ 69 6104.500000000003 36f60d45225e60c7da4558b070ce4b60 informatica_acessorios SP 68 

Databricks visualization. Run in Databricks to view.

Aqui, a consulta analisa se existe uma correlação entre o atraso na entrega dos produtos e as avaliações dos clientes. Este insight pode ajudar a melhorar a experiência do cliente, identificando problemas na cadeia de logística que afetam a satisfação do cliente, permitindo a melhoria dos tempos de entrega.

In [0]:
%sql
-- Correlação entre tempo de entrega e avaliação dos clientes

CREATE OR REPLACE VIEW VW_TEMPO_ENTREGA_AVALIACAO AS
SELECT 
    O.order_id,
    O.order_delivered_customer_date,
    O.order_estimated_delivery_date,
    R.review_score,
    DATEDIFF(O.order_delivered_customer_date, O.order_estimated_delivery_date) AS dias_atraso
FROM 
    olist_orders AS O
INNER JOIN 
    olist_order_reviews AS R ON O.order_id = R.order_id
WHERE 
    O.order_delivered_customer_date IS NOT NULL
    AND O.order_estimated_delivery_date IS NOT NULL;

In [0]:
%sql
SELECT * FROM VW_TEMPO_ENTREGA_AVALIACAO;

order_id order_delivered_customer_date order_estimated_delivery_date review_score dias_atraso d9eabc69f974b3d088e991cb7a7f08cd 2018-03-28T18:56:52.000+0000 2018-04-13T00:00:00.000+0000 4 16 c9fbf88f9c58364e0434971962dc1a53 2018-02-20T19:59:00.000+0000 2018-03-12T00:00:00.000+0000 5 20 fd01a48a7d75383a3623e71a538584c3 2017-08-28T17:04:11.000+0000 2017-08-31T00:00:00.000+0000 4 3 6d4616de4341417e17978fe57aec1c46 2017-05-05T15:56:20.000+0000 2017-05-24T00:00:00.000+0000 3 19 c606769bddf9fb8b9f949b128133c463 2017-06-23T13:14:54.000+0000 2017-07-10T00:00:00.000+0000 5 17 5ef95d0a45b4caaaa70e601665ba1a6a 2017-05-15T08:17:43.000+0000 2017-05-24T00:00:00.000+0000 5 9 9f2fe2350791b5e9e62610331d125843 2018-05-10T13:08:57.000+0000 2018-05-23T00:00:00.000+0000 5 13 86bf07c0a6d01d38dd8ecd1a1b68d139 2017-09-26T18:33:42.000+0000 2017-10-17T00:00:00.000+0000 5 21 2eb455a9ac809470168098ddf4e2a25b 2017-11-09T14:55:57.000+0000 2017-11-24T00:00:00.000+0000 5 15 5e4d2d8a6589ec90d1c82d0c2cb55eb0 2017-11-30T01:14:36.000+0000 2017-12-11T00:00:00.000+0000 4 11 098a8457920d6c63f0cb10ccfbcd369d 2018-06-12T12:41:20.000+0000 2018-06-25T00:00:00.000+0000 5 13 11d410c3e9ae90f2956cf43741d93347 2018-01-09T15:59:34.000+0000 2018-01-29T00:00:00.000+0000 5 20 f66696cb1765edf51ab4e07f41687f9e 2017-11-07T23:41:55.000+0000 2017-11-22T00:00:00.000+0000 4 15 c55fbaf625bec4b8ee5e7b0e8929bbc6 2018-03-21T19:40:44.000+0000 2018-04-03T00:00:00.000+0000 5 13 b90dbb242e04b393fad2f1df17bc90dc 2017-07-27T19:27:47.000+0000 2017-08-11T00:00:00.000+0000 5 15 c11e1e377e956e9d5bec2b0fa2ddc067 2018-07-04T22:18:33.000+0000 2018-07-17T00:00:00.000+0000 5 13 96a5b82a5f7b31928a21f1fe875e1caa 2017-06-26T12:17:21.000+0000 2017-07-12T00:00:00.000+0000 4 16 ff36f4d6d98c0b2a7e70acb7d1b3f139 2017-04-05T14:13:11.000+0000 2017-04-18T00:00:00.000+0000 4 13 3692c711f70b60feeedb43ae77e87980 2018-02-16T12:28:56.000+0000 2018-03-09T00:00:00.000+0000 4 21 c01eede39735860e68ef74a1d9ddf5cb 2017-12-27T18:54:45.000+0000 2018-01-16T00:00:00.000+0000 4 20 9f58be0e75ed0e5862bd6dbf261a8b05 2018-06-22T17:32:28.000+0000 2018-07-20T00:00:00.000+0000 3 28 a4e584c6dc40947a851d93c60fe9c50c 2018-08-09T01:03:23.000+0000 2018-08-09T00:00:00.000+0000 5 0 8024bee268e76b6cff9da86da00f1490 2017-03-22T13:34:35.000+0000 2017-03-31T00:00:00.000+0000 4 9 209e55ebe1b6ee30b02a4c07d7fc0cc8 2018-07-25T19:41:20.000+0000 2018-08-06T00:00:00.000+0000 5 12 47c001ba3d3d57aa11d52c45995d9e11 2018-03-28T20:46:58.000+0000 2018-03-20T00:00:00.000+0000 1 8 e5700a52207ef266413e9f43a7b0d5f6 2018-08-23T18:38:31.000+0000 2018-09-10T00:00:00.000+0000 5 18 282160d8e83b257c5105cac8f3ba2b63 2017-12-28T09:32:26.000+0000 2017-12-28T00:00:00.000+0000 3 0 61e268eee1d131498001b6121895c5ee 2018-01-05T19:34:22.000+0000 2018-01-19T00:00:00.000+0000 5 14 3351bf124a5c98aeee6b64f3ba214459 2017-08-17T15:33:22.000+0000 2017-08-31T00:00:00.000+0000 5 14 a501de32f4f7eba26aaa7864ec8dafb1 2018-02-01T12:58:32.000+0000 2018-02-19T00:00:00.000+0000 5 18 26f9b65f14088371f7c082c607f04d8c 2018-02-02T18:13:11.000+0000 2018-02-22T00:00:00.000+0000 5 20 6e68db908b8a2902c4f8309e1c1cbe3f 2017-11-16T18:04:47.000+0000 2017-11-28T00:00:00.000+0000 5 12 903103f3e4c9dfb4fd9224fd0f43d950 2018-01-03T20:58:47.000+0000 2018-01-12T00:00:00.000+0000 5 9 4d0de3f8be3ad40e85a5d6fe37054d9a 2017-12-22T21:35:24.000+0000 2017-12-26T00:00:00.000+0000 5 4 38639a0e5f4778171fd90e2233972555 2017-07-21T21:52:31.000+0000 2017-08-01T00:00:00.000+0000 5 11 d705acf2afc3dcdc3de7aefa1e0215cd 2018-05-05T00:07:42.000+0000 2018-05-14T00:00:00.000+0000 5 9 ba2018431e2b0cec56147edc7a0627a5 2018-05-11T22:47:33.000+0000 2018-05-25T00:00:00.000+0000 5 14 86dcddd0920dec11c6faa2276be53edf 2017-02-16T13:56:09.000+0000 2017-03-10T00:00:00.000+0000 5 22 6730796e2413628c3e327fbc24177a44 2017-08-28T19:37:45.000+0000 2017-09-15T00:00:00.000+0000 2 18 fc79bdcefc8fbd9f44f8cf9633793359 2017-02-03T16:42:04.000+0000 2017-03-02T00:00:00.000+0000 4 27 18846e52fc8a87bb5f3e3b353940b320 2017-12-23T17:23:25.000+0000 2018-01-08T00

Databricks visualization. Run in Databricks to view.

Este relatório foca nas categorias de produtos que geram mais vendas e receita. Ao analisar quais categorias de produtos estão a ser mais populares entre os consumidores, é possível ajustar a oferta de produtos, otimizar campanhas de marketing para as categorias de maior desempenho e entender as preferências de consumo em diferentes segmentos de mercado.

In [0]:
%sql
-- Categorias mais vendidas

CREATE OR REPLACE VIEW VW_CATEGORIAS_MAIS_VENDIDAS AS
SELECT 
    PCT.product_category_name_english,
    COUNT(OI.product_id) AS quantidade_vendida,
    SUM(OI.price) AS valor_total_vendido
FROM 
    olist_order_items AS OI
INNER JOIN 
    olist_products AS P ON OI.product_id = P.product_id
INNER JOIN 
    product_category_translation AS PCT ON P.product_category_name = PCT.product_category_name
GROUP BY 
    PCT.product_category_name_english
ORDER BY 
    valor_total_vendido DESC;

In [0]:
%sql
SELECT * FROM VW_CATEGORIAS_MAIS_VENDIDAS;

product_category_name_english quantidade_vendida valor_total_vendido health_beauty 9670 1258681.3399999938 watches_gifts 5991 1205005.679999998 bed_bath_table 11115 1036988.6799999807 sports_leisure 8641 988048.9699999838 computers_accessories 7827 911954.319999988 furniture_decor 8334 729762.4899999866 cool_stuff 3796 635290.8499999974 housewares 6964 632248.6599999928 auto 4235 592720.109999997 garden_tools 4347 485256.45999999647 toys 4117 483946.59999999864 baby 3065 411764.88999999897 perfumery 3419 399124.86999999976 telephony 4545 323667.5300000011 office_furniture 1691 273960.70000000007 stationery 2517 230943.23000000085 computers 203 222963.13 pet_shop 1947 214315.41000000035 musical_instruments 680 191498.8800000002 small_appliances 679 190648.58000000007 electronics 2767 160246.740000001 consoles_games 1137 157465.22000000026 fashion_bags_accessories 2031 152823.5400000008 construction_tools_construction 929 144677.5900000002 luggage_accessories 1092 140429.98000000048 home_appliances_2 238 113317.74000000002 home_construction 604 83088.12000000007 home_appliances 771 80171.53 agro_industry_and_commerce 212 72530.46999999999 furniture_living_room 503 68916.55999999997 fixed_telephony 264 59583.00000000002 home_confort 434 58572.03999999996 air_conditioning 297 55024.95999999999 audio 364 50688.49999999994 small_appliances_home_oven_and_coffee 76 47445.70999999999 books_general_interest 553 46856.87999999995 kitchen_dining_laundry_garden_furniture 281 46328.36999999997 construction_tools_lights 304 41079.999999999985 construction_tools_safety 194 40544.52 industry_commerce_and_business 268 39669.60999999999 food 510 29393.409999999963 market_place 311 28378.469999999983 costruction_tools_garden 238 25715.889999999996 art 209 24202.639999999992 fashion_shoes 262 23562.769999999982 drinks 379 22428.699999999975 signaling_and_security 199 21509.23 furniture_bedroom 109 20028.78 books_technical 267 19096.059999999994 costruction_tools_tools 103 15903.95 food_drink 278 15179.479999999992 fashion_male_clothing 132 10797.820000000003 fashion_underwear_beach 131 9541.550000000003 christmas_supplies 153 8800.820000000002 tablets_printing_image 83 7528.410000000001 cine_photo 72 6933.460000000001 music 38 6034.349999999999 dvds_blu_ray 64 5999.390000000001 books_imported 60 4639.85 party_supplies 43 4485.18 furniture_mattress_and_upholstery 38 4368.08 fashio_female_clothing 48 2803.6399999999994 fashion_sport 30 2119.5099999999998 la_cuisine 14 2054.99 arts_and_craftmanship 24 1814.0099999999998 diapers_and_hygiene 39 1567.59 flowers 33 1110.04 home_comfort_2 30 760.27 cds_dvds_musicals 14 730.0 fashion_childrens_clothes 8 569.85 security_and_services 2 283.28999999999996

Databricks visualization. Run in Databricks to view.

Esta consulta avalia o desempenho dos vendedores em termos de número de vendas, valor total das vendas e média de avaliações dos clientes. O insight resultante ajuda a identificar os vendedores com melhor performance, tanto em termos de volume de vendas quanto em qualidade de atendimento.

In [0]:
%sql
-- Desempenho dos vendedores

CREATE OR REPLACE VIEW VW_DESEMPENHO_VENDEDORES AS
SELECT 
    S.seller_id,
    S.seller_city,
    S.seller_state,
    COUNT(OI.order_id) AS total_vendas,
    SUM(OI.price) AS valor_total_vendas,
    AVG(ORR.review_score) AS media_avaliacoes
FROM 
    olist_sellers AS S
INNER JOIN 
    olist_order_items AS OI ON S.seller_id = OI.seller_id
INNER JOIN 
    olist_orders AS O ON OI.order_id = O.order_id
INNER JOIN 
    olist_order_reviews AS ORR ON O.order_id = ORR.order_id
GROUP BY 
    S.seller_id, S.seller_city, S.seller_state
ORDER BY 
    valor_total_vendas DESC;

In [0]:
%sql
SELECT * FROM VW_DESEMPENHO_VENDEDORES;

seller_id seller_city seller_state total_vendas valor_total_vendas media_avaliacoes 4869f7a5dfa277a7dca6462dcf3b52b2 guariba SP 1148 228071.04000000047 4.122822299651568 53243585a1d6dc2643021fd1853d8905 lauro de freitas BA 408 220740.05000000002 4.075980392156863 4a3ca9315b744ce9f8e9374361493884 ibitinga SP 1984 200561.42000000126 3.803931451612903 fa1c13f2614d7b5c4749cbc52fecda94 sumare SP 582 192774.43000000037 4.34020618556701 7c67e1448b00f6e969d365cea6b010ab itaquaquecetuba SP 1367 188017.85000000003 3.348207754206291 7e93a43ef30c4f03f38b393420bc753a barueri SP 339 176201.87999999998 4.206489675516224 da8622b14eb17ae2831f4ac5b9dab84a piracicaba SP 1568 161993.97000000117 4.071428571428571 7a67c85e85bb2ce8582c35f2203ad736 sao paulo SP 1166 141130.58000000034 4.234991423670669 1025f0e2d44d7041d6cf58b6550e0bfa sao paulo SP 1431 139484.3800000002 3.8497554157931515 955fee9216a65b617aa5c0531780ce60 sao paulo SP 1489 133948.81000000026 4.0517125587642715 46dc3b2cc0980fb8ec44634e21d2718e rio de janeiro RJ 535 126166.2600000003 4.181308411214953 6560211a19b47992c3666cc44a7e94c0 sao paulo SP 2020 122484.82 3.9094059405940595 620c87c171fb2a6dd6e8bb4dec959fc6 petropolis RJ 790 114015.3000000004 4.215189873417722 7d13fca15225358621be4086e1eb0964 ribeirao preto SP 574 113091.19000000005 4.001742160278746 5dceca129747e92ff8ef7a997dc4f8ca santa barbara d´oeste SP 342 110488.73000000011 3.991228070175439 1f50f920176fa81dab994f9023523100 sao jose do rio preto SP 1932 107002.21000000063 3.9824016563147 cc419e0650a3c5ba77189a1882b7556a santo andre SP 1811 106059.06000000089 4.0695748205411375 a1043bafd471dff536d0c462352beb48 ilicinea MG 767 101454.16000000018 4.189048239895698 3d871de0142ce09b7081e2b9d1733cb1 campo limpo paulista SP 1136 93960.80000000008 4.11443661971831 edb1ef5e36e0c8cd84eb3c9b003e486d teresopolis RJ 175 79284.55000000002 4.434285714285714 ccc4bbb5f32a6ab2b7066a4130f114e3 curitiba PR 191 73654.72 4.282722513089006 f7ba60f8c3f99e7ee4042fdef03b70c4 sao bernardo do campo SP 232 68780.0 4.211206896551724 8581055ce74af1daba164fdbd55a40de guarulhos SP 442 66054.49999999996 4.230769230769231 fe2032dab1a61af8794248c8196565c9 campinas SP 302 65205.61000000001 4.3841059602649 cca3071e3e9bb7d12640c9fbe2301306 ibitinga SP 831 64379.36999999992 3.851985559566787 04308b1ee57b6625f47df1d56f00eedf bombinhas SC 94 60130.59999999999 3.882978723404255 522620dcb18a6b31cd7bdf73665113a9 cascavel PR 176 56096.69999999999 3.897727272727273 37be5a7c751166fbc5f8ccba4119e043 sao paulo SP 282 55525.539999999986 4.301418439716312 218d46b86c1881d022bce9c68a7d4b15 ribeirao preto SP 427 55384.27999999999 4.142857142857143 25c5c91f63607446a97b143d2d535d31 itauna MG 273 55267.07999999999 3.7032967032967035 7ddcbb64b5bc1ef36ca8c151f6ec77df sao paulo SP 341 55266.589999999946 3.903225806451613 de722cd6dad950a92b7d4f82673f8833 recife PE 377 55126.29999999993 4.159151193633952 17e34d8224d27a541263c4c64b11a56b riberao preto SP 266 53376.15000000001 4.139097744360902 f5a590cf36251cf1162ea35bef76fe84 sao bernardo do campo SP 122 53201.78 4.237704918032787 e882b2a25a10b9c057cc49695f222c19 teresopolis RJ 60 52774.27 4.6 ceaec5548eefc6e23e6607c5435102e7 sao paulo SP 207 52062.18999999999 4.14975845410628 966cb4760537b1404caedd472cc610a5 diadema SP 75 51087.03999999999 3.8533333333333335 2bf6a2c1e71bbd29a4ad64e6d3c3629f nova friburgo RJ 31 50628.9 4.193548387096774 f8db351d8c4c4c22c6835c19a46f01b0 salto SP 722 50386.799999999836 4.218836565096953 b2ba3715d723d245138f291a6fe42594 sao paulo SP 360 49752.17999999992 4.108333333333333 17f51e7198701186712e53a39c564617 sao paulo SP 61 48019.0 4.344262295081967 77530e9772f57a62c906e1c21538ab82 curitiba PR 390 46897.49999999999 4.053846153846154 8160255418d5aaa7dbdc9f4c64ebda44 ibitinga SP 429 46654.88999999991 3.839160839160839 4e922959ae960d389249c378d1c939f5 jacarei SP 449 45466.369999999995 3.89532293986637 c826c40d7b19f62a09e2d7c5e7295ee2 guarulhos SP 371 45397.76000000001 4.0431266846361185 b33e7c55446eabf8fe1a42d037ac

Databricks visualization. Run in Databricks to view.